### DAY 2 summery

- xpec in terminal, see old example in exosat (optional read as a reminder of commands we run in class)
https://heasarc.gsfc.nasa.gov/docs/xanadu/xspec/manual/node38.html

- BEware chi/c statistics https://heasarc.gsfc.nasa.gov/xanadu/xspec/manual/XSappendixStatistics.html

- tutorial and fit on statistics (have a quick look we mentioned most info from slides in class)- http://labx.iasfbo.inaf.it/2014/resources/xspec_tutorial2014.pdf

- alphabetic list of models: https://heasarc.gsfc.nasa.gov/xanadu/xspec/manual/node129.html 

- MCMC https://heasarc.gsfc.nasa.gov/xanadu/xspec/manual/node43.html

- Bayessian statistics - Ultranest -- extra, not for class 
https://johannesbuchner.github.io/UltraNest/index.html


### VIDEO - and examples

Video with xspec in terminal by Garcia J.
https://www.youtube.com/watch?v=k1CD8f1LLhc

quick official tutorial
https://heasarc.gsfc.nasa.gov/xanadu/xspec/python/html/quick.html
extended 
https://heasarc.gsfc.nasa.gov/xanadu/xspec/python/html/extended.html

online example of a SNR Fe Kaplha line (just look commands and syntax)
https://gist.github.com/ivvv/716799056b4aadc87e41097472edbd20

Other example (complete.advanced)
https://github.com/mfacorcoran/pyxspec-tutorial/blob/master/PyXspecUserGuide-QuickTutorial.ipynb

Modeling and simulating spectra paper: https://arxiv.org/abs/2309.07577


### HOMEWORK... application in python

TODO: write a notebook and read data (src, bg, arf rmf) for the two sources in our image, and fit them with multiple models ie. (1) powerlaw (2) blackbody, with and without absorption ("pha*pow" or "pha*bbody"). In alphabetic listof models in xspce you will find multiple options for blackbody, like bbody, bbodyrad, notice the difference in normalization and what is the physical meaning.

Absorpion is crucial in X-rays so there are many advanced models, one of them beign "tbabs" (it is included in xspec), so try tbabs instead of simple "phabs" that contains absorption including molecules and grains. https://pulsar.sternwarte.uni-erlangen.de/wilms/research/tbabs/

Important notes and read examples
- sciserver jupyter or terminal does not have X11 capabilities, so "setp dev /xw" does not work. one can set devise in postscript or gif which should create a file that you can view.
see available options for device: https://heasarc.gsfc.nasa.gov/xanadu/xspec/manual/node114.html

- However setting a device in as "setplot dev /GIF" will not work automatically, sciserver is dum... so it might create multiple files with endidng *.gif_1 gif_2 etc. So one would need to rename them after every plot as *_1.gif in order to view them within sciserver. Best option.. use \null devise and work with matplotlib and plot object

- old exosat example in jupyter.../sciserver_cookbooks/


In [ ]:
import os

import xspec
from xspec import *

import matplotlib as mpl
# import re


from __future__ import print_function

import matplotlib.pyplot as plt
%matplotlib inline

In [ ]:
model = xspec.Model('tbabs*pow')


In [ ]:
Xset.abund = "wilm"
Xset.cosmo = "70 .0 0.73"
Xset.xsect = "vern"

In [ ]:
xspec.Plot.xAxis = "keV"
#xspec.Plot.device = "/xw" # this works only in the lab computer not in sciserver
xspec.Plot.device='/null'
xspec.Plot("model")

en = xspec.Plot.x()
enwid = xspec.Plot.xErr()
mop = xspec.Plot.model()

fig = plt.figure(figsize=[8,6])
plt.ylabel('Cts/s/keV', fontsize=12)
plt.xlabel('Energy (keV)', fontsize=12)
plt.title('SPEC fit: tbabs*pow', fontsize=12)
plt.plot(en,mop)

Try plot of a blackbody, notice peak energy, try plottting model or emodel (i.e. Energy*model) or eemodel, like we did in class

In [ ]:
model = xspec.Model('tbabs*bbody')

xspec.Plot("emodel")

en = xspec.Plot.x()
enwid = xspec.Plot.xErr()
mop = xspec.Plot.model()

plt.plot(en,mop)
#TODO,add units and axes. be carefull of emodel vs model vs eemodel, you need E or E^2 *cts/s/keV

lets plot model with differen absorption... Ok I will plot this for you but take notice how one can change values for parameters.. "model.TBabs.nh"

In [ ]:
model = xspec.Model('tbabs*pow')

nH = [0,0.1,1,10]

xspec.Plot("model")
en = xspec.Plot.x()
mop = xspec.Plot.model()

fig = plt.figure(figsize=[8,3])
plt.xscale('log')
plt.yscale('log')
plt.xlim([0.3,12])
plt.ylim([1e-8,100])


for ii in nH:
    model.TBabs.nH = ii   #<---- SEE THIS be carefull of how model object defines model parameters, try dir(model) next
    xspec.Plot("model")
    en = xspec.Plot.x()
    mop = xspec.Plot.model()
    plt.plot(en, mop, 'k--', alpha=0.2)

In [ ]:
dir(model)  # ... see TBabs and powerlaw or type "model." and press Tab to see what this object includes

### data laod and fit
load source and plot data, rebin and fit model...


In [ ]:
arf='arf1.arf'  ## BE carefull of PATHS if you use shared data.
rmf='swxpc0to12s6_20110101v014.rmf'
phafile = 'src1.pha'
bkg_spec_file = 'bg1.pha'
xspec.AllData.clear()
xspec.AllData("1:1 %s" % phafile)
xspec.AllData(1).response = rmf
xspec.AllData(1).response.arf = arf
xspec.AllData(1).background = bkg_spec_file

In [ ]:
AllData.ignore('**-0.5, 10.0-**')
AllData.ignore("bad")

AllData.show()

In [ ]:
model = xspec.Model('tbabs*pow')

xspec.Fit.statMethod = 'chi'
Fit.perform()

In [ ]:
# %matplotlib inline
xspec.Plot.setRebin(minSig=1.0,maxBins=500)
# xspec.Plot.setRebin(minSig=5.0,maxBins=50)

xspec.Plot.device='/null'
xspec.Plot.xAxis='keV'
xspec.Plot('lda del')
# xspec.Plot("lda","model","resid")
cr = xspec.Plot.y()
crerr = xspec.Plot.yErr()
en = xspec.Plot.x()
enwid = xspec.Plot.xErr()
mop = xspec.Plot.model()

resid = Plot.y(1,2)
eresid = Plot.yErr(1,2)
# eresid =resid*np.array(0)+1

fig = plt.figure(figsize=[8,6])
plt.ylabel('Cts/s/keV', fontsize=12)
plt.xlabel('Energy (keV)', fontsize=12)
plt.title('SPEC fit: wabs*bknpow', fontsize=12)
plt.yscale('log')
plt.xscale('log')
plt.errorbar(en, cr, xerr=enwid, yerr=crerr, fmt='k.', alpha=0.2)
plt.plot(en, mop,'r-')


fig = plt.figure(figsize=[8,3])
plt.ylabel('del chi', fontsize=12)
plt.xlabel('Energy (keV)', fontsize=12)
plt.xscale('log')
plt.axhline(0,ls=':',alpha=0.2,c='g')
plt.errorbar(en, resid, xerr=enwid, yerr=eresid, fmt='k.', alpha=0.2)

- BEware chi/c statistics https://heasarc.gsfc.nasa.gov/xanadu/xspec/manual/XSappendixStatistics.html

In [ ]:
model = xspec.Model('tbabs*pow')

#it is better to fit first with chi statistics then repeat with cstatistics, because c stat has sometimes problems converging
xspec.Fit.statMethod = 'chi'
Fit.perform()

xspec.Fit.statMethod = 'cstat'
Fit.perform()

### IMPORTANT .. rebin is only for visualization and plotting, does not affect fit statistics and the fit itself

In [ ]:
# %matplotlib inline
# xspec.Plot.setRebin(minSig=1.0,maxBins=500) 
xspec.Plot.setRebin(minSig=5.0,maxBins=50)

xspec.Plot.device='/null'
xspec.Plot.xAxis='keV'
xspec.Plot('lda del')
# xspec.Plot("lda","model","resid")
cr = xspec.Plot.y()
crerr = xspec.Plot.yErr()
en = xspec.Plot.x()
enwid = xspec.Plot.xErr()
mop = xspec.Plot.model()

resid = Plot.y(1,2)
eresid = Plot.yErr(1,2)
# eresid =resid*np.array(0)+1

fig = plt.figure(figsize=[8,6])
plt.ylabel('Cts/s/keV', fontsize=12)
plt.xlabel('Energy (keV)', fontsize=12)
plt.title('SPEC fit: wabs*bknpow', fontsize=12)
plt.yscale('log')
plt.xscale('log')
plt.errorbar(en, cr, xerr=enwid, yerr=crerr, fmt='k.', alpha=0.2)
plt.plot(en, mop,'r-')


fig = plt.figure(figsize=[8,3])
plt.ylabel('del chi', fontsize=12)
plt.xlabel('Energy (keV)', fontsize=12)
plt.xscale('log')
plt.axhline(0,ls=':',alpha=0.2,c='g')
plt.errorbar(en, resid, xerr=enwid, yerr=eresid, fmt='k.', alpha=0.2)

### TODO EXAMPE 2: repeat all above for src2

In [ ]:
arf='arf2.arf'  ## BE carefull of PATHS if you use shared data.
rmf='swxpc0to12s6_20110101v014.rmf'
phafile = 'src2.pha'
bkg_spec_file = 'bg2.pha'
xspec.AllData.clear()
xspec.AllData("1:1 %s" % phafile)
xspec.AllData(1).response = rmf
xspec.AllData(1).response.arf = arf
xspec.AllData(1).background = bkg_spec_file

### TODO EXAMPE 3: repeat all above for data in DAY2/XMM_Newton directory

In [ ]:
#THIS will give an error....

arf='XMM_Newton/pn_full.arf'  ## if not sure.. use full path for data... right click .. copy path
rmf='XMM_Newton/pn_full.rmf'
phafile = 'XMM_Newton/pnsource_spectrum_full.fits'
bkg_spec_file = 'XMM_Newton/pnbackground_spectrum.fits'
xspec.AllData.clear()
xspec.AllData("1:1 %s" % phafile)
# xspec.AllData(1).response = rmf
# xspec.AllData(1).response.arf = arf
# xspec.AllData(1).background = bkg_spec_file

### IMPORTANT The above gives an error because...
XMM data products have header keywords, that define rmf, arf and background files automatically.
Python tries to read a file in a subdirectory, and all other important files (rmf, arf and background ) are defined by relevant paths starting from main file (source spectrum) directory, ITS a MESS

solution... change directory via python, load data and return to working dir..

In [ ]:
os.getcwd()

In [ ]:
phafile = 'grouped_pn_full.fits'

PWD = os.getcwd()
os.chdir('/home/idies/workspace/Storage/EKPA_HEA/persistent/XRAY2024/DAY2/XMM_Newton/')
xspec.AllData.clear()
xspec.AllData("1:1 %s" % phafile)
os.chdir(PWD)

In [ ]:
AllData.ignore('**-0.5, 10.0-**')
AllData.ignore("bad")

AllData.show()

In [ ]:
xspec.Plot.setRebin(minSig=5.0,maxBins=50)

xspec.Plot.device='/null'
xspec.Plot.xAxis='keV'
xspec.Plot('ldata')

cr = xspec.Plot.y()
crerr = xspec.Plot.yErr()
en = xspec.Plot.x()
enwid = xspec.Plot.xErr()

fig = plt.figure(figsize=[8,6])
plt.ylabel('Cts/s/keV', fontsize=12)
plt.xlabel('Energy (keV)', fontsize=12)
plt.title('SPEC fit: Just DATA', fontsize=12)
plt.yscale('log')
plt.xscale('log')
plt.errorbar(en, cr, xerr=enwid, yerr=crerr, fmt='k.', alpha=0.2)


### Chalenge: 
Look at the above XMM newton plot, it is a plot of a White Dwarf, the spectrum is complex, and can be modeled by absorbed PL+BB i.e. tbabs*(pow+bbodyrad)
it is important to start fit with good initial conditions, i.e. soft black body (kT<0.5 keV) and a power-law for the high energy tail. Try to model the source (chi statistics should work fine as data are grouped in 25 counts per bin)